In [253]:
import pandas as pd
import numpy as np
import ast
import warnings
warnings.filterwarnings('ignore')

In [254]:
pd.reset_option('display.max_colwidth')
pd.reset_option('display.max_rows')
pd.reset_option('display.max_columns')

In [255]:
catalog_df = pd.read_csv('drive/MyDrive/collab_files/product_catalog.csv')
catalog_df

product_id  manufacturer_id  attribute_1  attribute_2  attribute_3  \
0           22665              861            4            0          490   
1           28640             1366           10            1          537   
2           13526             1090           10            0          511   
3           21399             1090           10            1          511   
4            8504              768            4            1          484   
...           ...              ...          ...          ...          ...   
32771       12036             1383           10            0          503   
32772       22709              567            4            2          491   
32773       32322             1385           10            1          500   
32774       19118             1113            6            2          491   
32775       16083             1111            4            3          485   

       attribute_4  attribute_5  \
0                2           66   
1                0          101   
2                0            0   
3                0            0   
4                0           66   
...            ...          ...   
32771            0          101   
32772            3           66   
32773            0           37   
32774            0          117   
32775            3           16   

                                              categories  
0                                [2890, 855, 3908, 3909]  
1                                                    NaN  
2      [3270, 163, 284, 1694, 12, 3837, 2422, 3595, 3...  
3                                                 [3270]  
4                                                 [2470]  
...                                                  ...  
32771  [3502, 1088, 2004, 691, 3422, 2308, 308, 3688,...  
32772     [3900, 3905, 3903, 3910, 1807, 274, 1467, 914]  
32773                                  [2686, 2609, 725]  
32774                 [3900, 3910, 3903, 2473, 914, 274]  
32775   [3900, 3901, 3905, 3902, 3903, 3910, 2473, 2470]  

[32776 rows x 8 columns]

In [366]:
catalog_df.loc[catalog_df['product_id']==5902]

product_id  manufacturer_id  attribute_1  attribute_2  attribute_3  \
17264        5902              193            4            0          453   

       attribute_4  attribute_5  \
17264            3          108   

                                                                     categories  
17264  [1160, 1373, 1522, 2754, 3254, 3532, 3900, 3901, 3902, 3903, 3910, 3977]

In [257]:
print("# -1 values in attributes")
for i in range(1,6):
  str1 = 'attribute_'+ str(i)
  print(f"{str1} : {catalog_df[catalog_df[str1]==-1]['product_id'].count()}")

# -1 values in attributes
attribute_1 : 4
attribute_2 : 0
attribute_3 : 466
attribute_4 : 617
attribute_5 : 4264


In [258]:
for i in range(1,5):
  str1 = 'attribute_'+ str(i)
  catalog_df[str1] = catalog_df[str1].replace(-1, catalog_df[str1].mode()[0])

In [259]:
pd.set_option('display.max_rows', None)       # Show all rows
# pd.set_option('display.max_columns', None)
pd.set_option('display.max_colwidth', None)


In [260]:
# Step 1: Calculate the mode for each group
mode_values = catalog_df.groupby(['attribute_1', 'attribute_2','attribute_3'])['categories'].agg(lambda x: pd.Series.mode(x).iloc[0] if not pd.Series.mode(x).empty else None)

# Step 2: Map the mode values back to the original DataFrame
catalog_df['mode_fill'] = catalog_df.set_index(['attribute_1', 'attribute_2','attribute_3']).index.map(mode_values)

# Step 3: Fill NaN values in 'categories' with the corresponding mode values
catalog_df['categories'].fillna(catalog_df['mode_fill'], inplace=True)

# Drop the temporary 'mode_fill' column if no longer needed
catalog_df.drop(columns=['mode_fill'], inplace=True)


In [261]:
catalog_df.isna().sum()

product_id           0
manufacturer_id      0
attribute_1          0
attribute_2          0
attribute_3          0
attribute_4          0
attribute_5          0
categories         197
dtype: int64

In [262]:
catalog_df['categories'].fillna(catalog_df['categories'].mode()[0],inplace=True)

In [263]:
catalog_df['categories'] = catalog_df['categories'].astype(str)

In [264]:
# catalog_df['categories'] = catalog_df['categories'].apply(ast.literal_eval)

In [265]:
# def assign_category(cat_list):
#     if len(cat_list) == 1 and isinstance(cat_list[0],int):
#         return int(cat_list[0])
#     for target in target_categories:
#         if target in cat_list:
#             return int(target)
#     return cat_list
# catalog_new = catalog_df.copy()
# catalog_new['categories'] = catalog_df['categories'].apply(assign_category)
# catalog_new.head(10)

In [266]:
# type(catalog_new.loc[32655,'categories'])

In [267]:
# # Filter rows where 'categories' column entries are not integers
# non_integer_rows = catalog_new[catalog_new['categories'].apply(lambda x: not isinstance(x, int))].reset_index(drop=True)
# len(non_integer_rows)

In [268]:
# from collections import Counter


# # String formatındaki listeleri dönüştürme
# # Tüm kategorileri bir araya getirme
# all_categories = [item for sublist in non_integer_rows['categories'] for item in sublist]

# # En çok tekrar eden kategorileri bulma
# category_counts = Counter(all_categories)
# most_common_categories = category_counts.most_common(20)

# # Sonucu yazdırma
# print(most_common_categories)


In [269]:
category_map_df = pd.read_csv("/content/drive/MyDrive/collab_files/product_category_map.csv")
category_map_df.head()

category_id  parent_category_id
0            0                  75
1            1                1499
2            2                1082
3            3                3498
4            4                1623

In [270]:
category_map_df = category_map_df.drop_duplicates(subset=['category_id'])
category_map_df[category_map_df['category_id'].duplicated(keep=False)]

Empty DataFrame
Columns: [category_id, parent_category_id]
Index: []

In [271]:
category_map_df[category_map_df['category_id']==category_map_df['parent_category_id']]['category_id'].values

array([3898])

In [272]:
category_map_df.loc[category_map_df['category_id'] == 3908, 'parent_category_id']


3940    3898
Name: parent_category_id, dtype: int64

In [273]:
def category_mapper(df):
  top_nodes = df[df['category_id']==df['parent_category_id']]['category_id'].values
  category_map_df_filtered = df.copy()
  category_map_df_filtered.loc[category_map_df_filtered['parent_category_id'].isin(top_nodes),'parent_category_id']=category_map_df_filtered['category_id']
  parent_list=category_map_df_filtered[category_map_df_filtered['category_id']==category_map_df_filtered['parent_category_id']]['category_id'].values
  parent_list = [x for x in parent_list if x <= 3898]
  return category_map_df_filtered,parent_list


In [274]:
catalog_df['categories'] = catalog_df['categories'].apply(ast.literal_eval)
catalog_df['categories'] = catalog_df['categories'].apply(lambda x: sorted(x))
catalog_df.loc[0,'categories']

[855, 2890, 3908, 3909]

In [275]:
def category_row_transform(row, df_map, parents):
    category = row['categories']
    element_list = []
    for element in category:
      while element not in parents:
          element = df_map.loc[df_map['category_id'] == element, 'parent_category_id'].values[0]
      element_list.append(element)
    category = list(set(element_list))
    row['categories'] = category
    return row


In [276]:
category_map_df_filtered, parent_list = category_mapper(category_map_df)

In [277]:
category_map_df_filtered.loc[category_map_df_filtered['parent_category_id'] >= 3898, 'parent_category_id'] = 3898
category_map_df_filtered = category_map_df_filtered.drop_duplicates(subset=['category_id', 'parent_category_id'])

In [278]:
catalog_df_transformed = catalog_df.apply(lambda row: category_row_transform(row,category_map_df_filtered,parent_list),axis=1)

In [279]:
catalog_df_transformed.loc[0,'categories']

[3898, 2012, 2838]

In [280]:
from collections import Counter
def similar_categories(category,similar_count):
  filtered_categories = catalog_df_transformed[
      catalog_df_transformed['categories'].apply(lambda x: isinstance(x, list) and category in x)
  ]['categories']

  # Flatten the filtered lists into a single list
  all_elements = [item for sublist in filtered_categories for item in sublist]

  # Count occurrences of each element
  value_counts = Counter(all_elements)

  # Convert to a sorted DataFrame for better presentation
  value_counts_df = pd.DataFrame(value_counts.items(), columns=['Category', 'Count']).sort_values(by='Count', ascending=False)

  return value_counts_df.iloc[1:similar_count+1, 0].tolist()


In [297]:
similar_categories(1825,5)

[366, 1677, 3898, 3624, 2364]

In [294]:
vcounts= catalog_df_transformed['categories'].value_counts()
len(vcounts)

3284

In [296]:
vcounts.head(39)

categories
[34]                      3294
[1072]                    2937
[1825, 366]                981
[2346]                     905
[3898, 2012]               785
[3189]                     752
[275, 965]                 734
[3860]                     730
[252, 519]                 728
[1682, 3898]               547
[2793]                     518
[2723, 519]                502
[686]                      494
[3056, 3898]               417
[275, 2364, 965]           384
[1072, 3898]               355
[3330, 959]                352
[2917, 1735]               343
[3504]                     326
[34, 2364]                 319
[3616, 366]                308
[1825, 1677, 366]          304
[1072, 2793]               297
[3288, 875]                289
[34, 3898]                 281
[2364]                     278
[298, 678]                 272
[3616, 2006]               260
[1072, 2364]               214
[370]                      213
[3898]                     208
[366]                      137
[3898, 366]                137
[2928, 275, 2364, 965]     127
[2364, 3189]               127
[3616, 2364, 2006]         124
[2364, 3860]               123
[432, 1677, 366]           121
[432]                      115
Name: count, dtype: int64

In [298]:
transactions_df= pd.read_csv("drive/MyDrive/collab_files/transactions.csv")
transactions_df.head()


customer_id  product_id purchase_date  quantity
0        38769        3477    2020-06-01         1
1        42535       30474    2020-06-01         1
2        42535       15833    2020-06-01         1
3        42535       20131    2020-06-01         1
4        42535        4325    2020-06-01         1

In [299]:
train_start = transactions_df.merge(catalog_df_transformed, on='product_id', how='left')
train_start= train_start.drop(columns=['manufacturer_id','quantity'])
train_start.head()

customer_id  product_id purchase_date  attribute_1  attribute_2  \
0        38769        3477    2020-06-01            6            0   
1        42535       30474    2020-06-01           10            3   
2        42535       15833    2020-06-01            4            1   
3        42535       20131    2020-06-01            4            0   
4        42535        4325    2020-06-01            6            0   

   attribute_3  attribute_4  attribute_5  \
0          196            0           45   
1          229            3          132   
2          455            0          108   
3          291            3           44   
4          303            0           45   

                                                    categories  
0                                           [3056, 3898, 1543]  
1                                [1666, 621, 3056, 3898, 2364]  
2                                             [3624, 252, 519]  
3  [1763, 3624, 2793, 2762, 621, 1682, 1557, 2231, 3898, 1565]  
4                               [3624, 1682, 2231, 3898, 2364]

In [352]:
cust= train_start.loc[train_start['customer_id'] == 61,:].sort_values(by=['purchase_date'])
cust

customer_id  product_id purchase_date  attribute_1  attribute_2  \
172436            61       19681    2020-07-10           10            0   
224261            61        4648    2020-07-23            4            3   
258987            61        4648    2020-08-01            4            3   
312106            61       24296    2020-08-14           10            0   
312122            61       28291    2020-08-14            6            0   
404486            61       20131    2020-09-05            4            0   
404487            61       28554    2020-09-05            4            0   
448941            61        4648    2020-09-16            4            3   
514407            61        5654    2020-10-02            4            0   
514406            61         637    2020-10-02            4            0   
514388            61       32752    2020-10-02            4            1   
514387            61        7913    2020-10-02           10            0   
711148            61       30157    2020-11-21            4            0   
711366            61       10805    2020-11-21            4            0   
711374            61       26072    2020-11-21            4            0   
711386            61        9649    2020-11-21            4            0   
711387            61       20131    2020-11-21            4            0   
711396            61       14833    2020-11-21           10            0   
711405            61       23582    2020-11-21            4            0   
1028415           61       20204    2021-01-24            6            0   

         attribute_3  attribute_4  attribute_5  \
172436           425            0          132   
224261           491            3          144   
258987           491            3          144   
312106           421            3           25   
312122           232            3          122   
404486           291            3           44   
404487            21            3           52   
448941           491            3          144   
514407           371            0           89   
514406           131            0          144   
514388           290            0           44   
514387           345            0           95   
711148           491            0          144   
711366           485            3          144   
711374           370            3           89   
711386           444            3           66   
711387           291            3           44   
711396           491            3           39   
711405            21            3           52   
1028415          221            3           17   

                                                          categories  
172436                                       [3898, 2723, 519, 2231]  
224261                                       [1072, 3898, 621, 2006]  
258987                                       [1072, 3898, 621, 2006]  
312106                                                   [2723, 519]  
312122                                                  [3056, 3898]  
404486   [1763, 3624, 2793, 2762, 621, 1682, 1557, 2231, 3898, 1565]  
404487                                             [857, 3898, 2012]  
448941                                       [1072, 3898, 621, 2006]  
514407                                [2793, 1840, 2105, 3898, 2364]  
514406                                             [3624, 2364, 686]  
514388                                      [3624, 1682, 3898, 1543]  
514387                                                  [3624, 2793]  
711148                                                        [1072]  
711366                                                  [1072, 3898]  
711374              [3624, 2793, 2762, 3409, 3540, 2231, 3898, 2364]  
711386                     [2762, 875, 1840, 3860, 3288, 3898, 2364]  
711387   [1763, 3624, 2793, 2762, 621, 1682, 1557, 2231, 3898, 1565]  
711396                      [1763, 2723, 519, 2346, 686, 1072, 3898]  
711405      

In [374]:
def cust_similarity_calculator(customer,product,neig_count=1):
  cust= train_start.loc[train_start['customer_id'] == customer,:].sort_values(by=['purchase_date'])
  cust_product= catalog_df_transformed.loc[catalog_df_transformed['product_id'] == product ,:].iloc[0]
  lst = cust_product.categories

  for category in categories:
    lst = lst + similar_categories(category,neig_count)  # Get the list of similar categories
  lst = list(set(lst))

  cust['similar'] = 0
  for category in lst:
      # Update the 'similar' column to 1 where the category is found in the 'categories' column
      cust.loc[cust['categories'].apply(lambda x: isinstance(x, list) and category in x), 'similar'] = 1

  att1 = cust_product['attribute_1']
  att2 = cust_product['attribute_2']
  att3 = cust_product['attribute_3']
  att4 = cust_product['attribute_4']
  att5 = cust_product['attribute_5']
  cust.reset_index(drop=True,inplace=True)
  for i in range(1, len(cust)):  # Start from index 1 to compare with previous row
      if cust.loc[i, 'attribute_1'] == att1:
          cust.loc[i, 'similar'] += 1
      if cust.loc[i, 'attribute_2'] == att2:
          cust.loc[i, 'similar'] += 1
      if cust.loc[i, 'attribute_3'] == att3:
          cust.loc[i, 'similar'] += 1
      if cust.loc[i, 'attribute_4'] == att4:
          cust.loc[i, 'similar'] += 1
      if cust.loc[i, 'attribute_5'] == att5:
          cust.loc[i, 'similar'] += 1
  return cust

In [386]:
def week_value_calculator(customer,product,neighbour):
  cust = cust_similarity_calculator(customer,product,neighbour)
  cust = cust[cust['similar']>=3]

  cust['purchase_date'] = pd.to_datetime(cust['purchase_date'])
  cust_final = cust.drop_duplicates(subset=['purchase_date'])
  cust_final = cust_final.sort_values(by='purchase_date', ascending=True)
  # Calculate the difference in days between consecutive rows
  cust_final['days_diff'] = cust_final['purchase_date'].diff().dt.days
  cust_final.dropna(subset=['days_diff'], inplace=True)

  cust_final['weeks_diff'] = np.ceil(cust_final['days_diff'] / 7).astype(int)
  cust_final['weeks_diff'] = cust_final['weeks_diff'].clip(upper=4)


  return cust_final

In [415]:
train = week_value_calculator(130,6639,1)
train

customer_id  product_id purchase_date  attribute_1  attribute_2  \
6           130        6639    2020-07-11            4            3   
11          130       26940    2020-07-12            4            0   
15          130       18775    2020-07-30            4            0   
18          130        6639    2020-09-13            4            3   
21          130       26940    2020-09-19            4            0   
24          130       15155    2020-10-17            4            0   
36          130       10376    2020-12-12            4            0   

    attribute_3  attribute_4  attribute_5                      categories  \
6           487            3          144         [1072, 875, 2364, 3288]   
11          487            3           44              [1072, 2346, 3898]   
15          491            3          144               [1072, 3898, 686]   
18          487            3          144         [1072, 875, 2364, 3288]   
21          487            3           44              [1072, 2346, 3898]   
24          291            3           44              [3624, 2793, 3898]   
36          535            3          105  [2920, 2793, 2762, 2231, 3898]   

    similar  days_diff  weeks_diff  
6         6       26.0           4  
11        4        1.0           1  
15        4       18.0           3  
18        6       45.0           4  
21        4        6.0           1  
24        3       28.0           4  
36        3       56.0           4

In [429]:
def prediction(customer,product,neighbour):
  train = week_value_calculator(customer,product,neighbour)
  min_date = train['purchase_date'].min()
  max_date = train['purchase_date'].max()
  date_range = pd.date_range(start=min_date, end=max_date, freq='M')
  date_range_months = len(date_range)
  smaller_than_4 = len(train[train['days_diff'] < 31])
  if date_range_months > smaller_than_4:
    return 0
  pred = train['weeks_diff'].mean()
  return pred.round()

In [430]:
prediction(61,4648,1)

0

In [431]:
test_df= pd.read_csv("drive/MyDrive/collab_files/test.csv")
pairs_list = test_df[['id','customer_id', 'product_id']].values.tolist()
pairs_list[:5]

[[0, 0, 20664], [1, 0, 28231], [2, 13, 2690], [3, 15, 1299], [4, 15, 20968]]

In [ ]:
output_data = []
i=0
for lst in pairs_list:
    i+=1
    print(i)
    id,c, p = lst  # Extract customer_id and product_id
    try:
      pw = prediction(c, p, 1)  # Get prediction
    except:
      pw = 0

    # Append the result to output_data list
    output_data.append({
        'id': id,  # Assuming you want to add an ID later or from somewhere else
        'customer_id': c,
        'product_id': p,
        'prediction': pw
    })

# Convert the list of dictionaries into a DataFrame
output_df = pd.DataFrame(output_data)
output_df

1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
68
69
70
71
72
73
74
75
76
77
78
79
80
81
82
83
84
85
86
87
88
89
90
91
92
93
94
95
96
97
98
99
100
101
102
103
104
105
106
107
108
109
110
111
112
113
114
115
116
117
118
119
120
121
122
123
124
125
126
127
128
129
130
131
132
133
134
135
136
137
138
139
140
141
142
143
144
145
146
147
148
149
150
151
152
153
154
155
156
157
158
159
160
161
162
163
164
165
166
167
168
169
170
171
172
173
174
175
176
177
178
179
180
181
182
183
184
185
186
187
188
189
190
191
192
193
194
195
196
197
198
199
200
201
202
203
204
205
206
207
208
209
210
211
212
213
214
215
216
217
218
219
220
221
222
223
224
225
226
227
228
229
230
231
232
233
234
235
236
237
238
239
240
241
242
243
244
245
246
247
248
249
250
251
252
253
254
255
256
257
258
259
260
261
262
263
264
265
266
267
268
269
270
271
272
273
274
275
276
277


In [ ]:
output_df[output_df['prediction']>4]=0
output_df['prediction']=output_df['prediction'].astype(int)
output_df

id  customer_id  product_id  prediction
0        0            0       20664           0
1        0            0           0           0
2        2           13        2690           4
3        3           15        1299           3
4        4           15       20968           3
5        5           20        8272           0
6        6           24       11340           2
7        7           34       21146           3
8        8           34       31244           3
9        0            0           0           0
10      10           61        4648           0
11      11           76        4603           3
12      12           76       23869           4
13      13           76       29829           3
14      14           78       12635           0
15      15           79       21856           4
16      16           80        5907           0
17      17           94        2747           4
18      18           94       17291           3
19      19           94       20338           3
20      20           99        5076           0
21      21          100        5891           0
22      22          110       11155           4
23      23          115       19573           0
24      24          124       20133           4
25      25          129       23582           0
26      26          130        2446           4
27      27          130        6639           4
28      28          130       18586           4
29      29          130       24236           4
30      30          134        4595           3
31      31          134        5902           4
32      32          135         190           4
33      33          135       16809           4
34      34          148       31812           0
35      35          149       31265           3
36      36          151       14776           3
37      37          156        3957           3
38      38          164        9757           4
39      39          167       12528           4
40      40          169         875           4
41      41          169        4439           0
42      42          169        6923           4
43      43          169       29497           4
44      44          170       24528           2
45      45          186       28135           4
46      46          189        2062           0
47      47          190       24243           0
48      48          190       26273           0
49      49          197       15523           3
50      50          209        6105           3
51      51          209       28900           3
52      52          210       11251           4
53      53          218        2446           3
54      54          218       11434           3
55      55          218       29307           0
56      56          225        4702           3
57      57          232        2065           4
58      58          232       27629           4
59      59          236       28695           2
60      60          239       11074           0
61      61          240       10846           3
62      62          240       11556           3
63       0            0           0           0
64      64          258       17645           0
65      65          264       12192           2
66      66          277        2517           2
67      67          277       32204           2
68      68          312          23           3
69      69          312       13676           2
70      70          314       27830           0
71      71          319        6169           3
72      72          324        1924           3
73      73          328       21690           0
74       0            0           0           0
75      75          369        5391           4
76      76          369       12528           4
77      77          377       32204           0
78      78          378        2517           3
79      79          384       30448           4
80      80          386        8168           0
81      81          388       19837           3
82      82          390 

In [ ]:
X_test.head()

In [ ]:
X_test['categories'] = X_test['categories'].astype(str)
X_test['categories'] = X_test['categories'].apply(ast.literal_eval)


In [ ]:
X_test = X_test.apply(lambda row: category_row_transform(row,category_map_df_filtered,parent_list),axis=1)

In [ ]:
X_test.loc[X_test['categories'] == 182, 'categories'] = 34
X_test.loc[X_test['categories'] == 336, 'categories'] = 366
X_test.loc[X_test['categories'] == 252, 'categories'] = 275
X_test.loc[X_test['categories'] >= 3898, 'categories'] = 3898
X_test.loc[X_test['categories'] == 422, 'categories'] = 432
X_test.loc[X_test['categories'] == 678, 'categories'] = 686
X_test.loc[X_test['categories'] == 857, 'categories'] = 875
X_test.loc[X_test['categories'] == 1062, 'categories'] = 1072
X_test.loc[X_test['categories'] == 1557, 'categories'] = 1559
X_test.loc[X_test['categories'] == 1565, 'categories'] = 1559
X_test.loc[X_test['categories'] == 1666, 'categories'] = 1677
X_test.loc[X_test['categories'] == 2011, 'categories'] = 2012
X_test.loc[X_test['categories'] == 2209, 'categories'] = 2109
X_test.loc[X_test['categories'] == 2346, 'categories'] = 2364
X_test.loc[X_test['categories'] == 3283, 'categories'] = 3288
X_test.loc[X_test['categories'] == 3540, 'categories'] = 3504
X_test.loc[X_test['categories'] == 3613, 'categories'] = 3617
X_test.loc[X_test['categories'] == 3616, 'categories'] = 3617
X_test.loc[X_test['categories'] == 3752, 'categories'] = 3852

In [ ]:
X_test.drop(columns=['manufacturer_id','id'],inplace=True)
X_test.head()

In [ ]:
test_cluster = X_test.merge(customer_encoded[['customer_id', 'cluster']], on='customer_id', how='left')
test_cluster.head()

In [ ]:
test_cluster.drop(columns=['customer_id','product_id'],inplace=True)

In [ ]:
test_cluster.head()

In [ ]:
# Ensure predictions are made for each row by reshaping the data correctly
test_cluster["prediction"] = test_cluster.apply(
    lambda row: model_list[int(row["cluster"])].predict(row.drop(["cluster", "prediction"]).values.reshape(1, -1))[0],
    axis=1
)
test_cluster.head()


In [ ]:
test_cluster["prediction"].value_counts()


In [ ]:

output_df = pd.DataFrame({
    'id': test_df['id'],
    'customer_id': test_df['customer_id'],
    'product_id': test_df['product_id'],
    'prediction': test_cluster["prediction"]
})

# Display the output DataFrame
print(output_df)

# Optionally, save the output to a CSV file
output_df.to_csv('predictions_output.csv', index=False)


In [ ]:
len(output_df)

10000

In [ ]:
train_cluster[train_cluster['customer_id']==46049]

In [ ]:
output_df.to_csv('predictions_output.csv', index=False)


In [ ]:
test_df= pd.read_csv("drive/MyDrive/collab_files/test.csv")
test_df

id  customer_id  product_id  prediction
0        0            0       20664         NaN
1        1            0       28231         NaN
2        2           13        2690         NaN
3        3           15        1299         NaN
4        4           15       20968         NaN
5        5           20        8272         NaN
6        6           24       11340         NaN
7        7           34       21146         NaN
8        8           34       31244         NaN
9        9           46       31083         NaN
10      10           61        4648         NaN
11      11           76        4603         NaN
12      12           76       23869         NaN
13      13           76       29829         NaN
14      14           78       12635         NaN
15      15           79       21856         NaN
16      16           80        5907         NaN
17      17           94        2747         NaN
18      18           94       17291         NaN
19      19           94       20338         NaN
20      20           99        5076         NaN
21      21          100        5891         NaN
22      22          110       11155         NaN
23      23          115       19573         NaN
24      24          124       20133         NaN
25      25          129       23582         NaN
26      26          130        2446         NaN
27      27          130        6639         NaN
28      28          130       18586         NaN
29      29          130       24236         NaN
30      30          134        4595         NaN
31      31          134        5902         NaN
32      32          135         190         NaN
33      33          135       16809         NaN
34      34          148       31812         NaN
35      35          149       31265         NaN
36      36          151       14776         NaN
37      37          156        3957         NaN
38      38          164        9757         NaN
39      39          167       12528         NaN
40      40          169         875         NaN
41      41          169        4439         NaN
42      42          169        6923         NaN
43      43          169       29497         NaN
44      44          170       24528         NaN
45      45          186       28135         NaN
46      46          189        2062         NaN
47      47          190       24243         NaN
48      48          190       26273         NaN
49      49          197       15523         NaN
50      50          209        6105         NaN
51      51          209       28900         NaN
52      52          210       11251         NaN
53      53          218        2446         NaN
54      54          218       11434         NaN
55      55          218       29307         NaN
56      56          225        4702         NaN
57      57          232        2065         NaN
58      58          232       27629         NaN
59      59          236       28695         NaN
60      60          239       11074         NaN
61      61          240       10846         NaN
62      62          240       11556         NaN
63      63          256       27263         NaN
64      64          258       17645         NaN
65      65          264       12192         NaN
66      66          277        2517         NaN
67      67          277       32204         NaN
68      68          312          23         NaN
69      69          312       13676         NaN
70      70          314       27830         NaN
71      71          319        6169         NaN
72      72          324        1924         NaN
73      73          328       21690         NaN
74      74          332        8004         NaN
75      75          369        5391         NaN
76      76          369       12528         NaN
77      77          377       32204         NaN
78      78          378        2517         NaN
79      79          384       30448         NaN
80      80          386        8168         NaN
81      81          388       19837         NaN
82      82          390 

In [ ]:
test_df["prediction"] = output_df['prediction']
test_df

id  customer_id  product_id  prediction
0        0            0       20664           0
1        1            0       28231           0
2        2           13        2690           4
3        3           15        1299           3
4        4           15       20968           3
5        5           20        8272           0
6        6           24       11340           2
7        7           34       21146           3
8        8           34       31244           3
9        9           46       31083           0
10      10           61        4648           0
11      11           76        4603           3
12      12           76       23869           4
13      13           76       29829           3
14      14           78       12635           0
15      15           79       21856           4
16      16           80        5907           0
17      17           94        2747           4
18      18           94       17291           3
19      19           94       20338           3
20      20           99        5076           0
21      21          100        5891           0
22      22          110       11155           4
23      23          115       19573           0
24      24          124       20133           4
25      25          129       23582           0
26      26          130        2446           4
27      27          130        6639           4
28      28          130       18586           4
29      29          130       24236           4
30      30          134        4595           3
31      31          134        5902           4
32      32          135         190           4
33      33          135       16809           4
34      34          148       31812           0
35      35          149       31265           3
36      36          151       14776           3
37      37          156        3957           3
38      38          164        9757           4
39      39          167       12528           4
40      40          169         875           4
41      41          169        4439           0
42      42          169        6923           4
43      43          169       29497           4
44      44          170       24528           2
45      45          186       28135           4
46      46          189        2062           0
47      47          190       24243           0
48      48          190       26273           0
49      49          197       15523           3
50      50          209        6105           3
51      51          209       28900           3
52      52          210       11251           4
53      53          218        2446           3
54      54          218       11434           3
55      55          218       29307           0
56      56          225        4702           3
57      57          232        2065           4
58      58          232       27629           4
59      59          236       28695           2
60      60          239       11074           0
61      61          240       10846           3
62      62          240       11556           3
63      63          256       27263           0
64      64          258       17645           0
65      65          264       12192           2
66      66          277        2517           2
67      67          277       32204           2
68      68          312          23           3
69      69          312       13676           2
70      70          314       27830           0
71      71          319        6169           3
72      72          324        1924           3
73      73          328       21690           0
74      74          332        8004           0
75      75          369        5391           4
76      76          369       12528           4
77      77          377       32204           0
78      78          378        2517           3
79      79          384       30448           4
80      80          386        8168           0
81      81          388       19837           3
82      82          390 

In [ ]:
test_df.to_csv('1predictions_output.csv', index=False)